In [1]:
import gradio as gr
import torch
import numpy as np
import matplotlib.pyplot as plt
from test_functions.Ackley10D import *
from test_functions.Ackley2D import *
from test_functions.Ackley6D import *
from test_functions.HeatExchanger import *
from test_functions.CantileverBeam import *
from test_functions.Car import *
from test_functions.CompressionSpring import *
from test_functions.GKXWC1 import *
from test_functions.GKXWC2 import *
from test_functions.HeatExchanger import *
from test_functions.JLH1 import *
from test_functions.JLH2 import *
from test_functions.KeaneBump import *
from test_functions.GKXWC1 import *
from test_functions.GKXWC2 import *
from test_functions.PressureVessel import *
from test_functions.ReinforcedConcreteBeam import *
from test_functions.SpeedReducer import *
from test_functions.ThreeTruss import *
from test_functions.WeldedBeam import *
# Import other objective functions as needed
import time

from Rosen_PFN4BO import *

def optimize(objective_function, iteration_input):

    # Variable setup
    Current_BEST = -1e10   # Some arbitrary very small number
    Prev_BEST = -1e10

    # Initial random samples
    # print(objective_functions)
    trained_X = torch.rand(20, objective_functions[objective_function]['dim'])

    # Scale it to the domain of interest using the selected function
    # print(objective_function)
    X_Scaled = objective_functions[objective_function]['scaling'](trained_X)

    # Get the constraints and objective
    trained_gx, trained_Y = objective_functions[objective_function]['function'](X_Scaled)

    # Convergence list to store best values
    convergence = []

    START_TIME = time.time()

    # Optimization Loop
    for ii in range(iteration_input):  # Example with 100 iterations

        # (0) Get the updated data for this iteration
        X_scaled = objective_functions[objective_function]['scaling'](trained_X)
        trained_gx, trained_Y = objective_functions[objective_function]['function'](X_scaled)

        # (1) Randomly sample Xpen 
        X_pen = torch.rand(1000,trained_X.shape[1])

        # (2) PFN inference phase with EI
        default_model = 'final_models/Cyril_500features_800epoch_cpu.pt'
        
        ei, p_feas = Rosen_PFN_Parallel(default_model,
                                           trained_X, 
                                           trained_Y, 
                                           trained_gx,
                                           X_pen,
                                           'power',
                                           'ei'
                                          )

        # Calculating CEI
        CEI = ei
        for jj in range(p_feas.shape[1]):
            CEI = CEI*p_feas[:,jj]

        # (4) Get the next search value
        rec_idx = torch.argmax(CEI)
        best_candidate = X_pen[rec_idx,:].unsqueeze(0)

        # (5) Append the next search point
        trained_X = torch.cat([trained_X, best_candidate])


        ################################################################################
        # This is just for visualizing the best value. 
        # This section can be remove for pure optimization purpose
        Current_X = objective_functions[objective_function]['scaling'](trained_X)
        Current_GX, Current_Y = objective_functions[objective_function]['function'](Current_X)
        if ((Current_GX<=0).all(dim=1)).any():
            Current_BEST = torch.max(Current_Y[(Current_GX<=0).all(dim=1)])
        else:
            Current_BEST = Prev_BEST
        ################################################################################
        
        # (ii) Convergence tracking (assuming the best Y is to be maximized)
        if Current_BEST != -1e10:
            convergence.append(Current_BEST.abs())

    # Timing
    END_TIME = time.time()
    TOTAL_TIME = END_TIME - START_TIME
    
    # Website visualization
    # (i) Radar chart for trained_X
    radar_chart = create_radar_chart(X_scaled)
    # (ii) Convergence tracking (assuming the best Y is to be maximized)
    convergence_plot = create_convergence_plot(convergence, TOTAL_TIME)
    
    return radar_chart, convergence_plot

def create_radar_chart(X_scaled):
    fig, ax = plt.subplots(figsize=(6, 6), subplot_kw=dict(polar=True))
    labels = [f'x{i+1}' for i in range(X_scaled.shape[1])]
    values = X_scaled.mean(dim=0).numpy()
    
    num_vars = len(labels)
    angles = np.linspace(0, 2 * np.pi, num_vars, endpoint=False).tolist()
    values = np.concatenate((values, [values[0]]))
    angles += angles[:1]

    ax.fill(angles, values, color='green', alpha=0.25)
    ax.plot(angles, values, color='green', linewidth=2)
    ax.set_yticklabels([])
    ax.set_xticks(angles[:-1])
    # ax.set_xticklabels(labels)
    ax.set_xticklabels([f'{label}\n({value:.2f})' for label, value in zip(labels, values[:-1])])  # Show values
    ax.set_title("Selected Design", size=15, color='black', y=1.1)
    
    plt.close(fig)
    return fig

def create_convergence_plot(convergence, TOTAL_TIME):
    fig, ax = plt.subplots()
    # print(len(convergence))
    ax.plot(convergence, label='Best Objective Value')
    ax.set_xlabel('Iteration')
    ax.set_ylabel('Objective Value')
    ax.set_title('Convergence Plot (Opt Runtime: {t} sec)'.format(t=round(TOTAL_TIME, 2)))
    ax.legend()

    # Add text to the top right corner of the plot
    if len(convergence) == 0:
        ax.text(0.5, 0.5, 'No Feasible Design Found', transform=ax.transAxes, fontsize=12,
                verticalalignment='top', horizontalalignment='right')
    
    plt.close(fig)
    return fig

# Define available objective functions
objective_functions = {
    "Ackley2D": {"function": Ackley2D, "scaling": Ackley2D_Scaling, "dim": 2},
    "Ackley6D": {"function": Ackley6D, "scaling": Ackley6D_Scaling, "dim": 6},
    "Ackley10D": {"function": Ackley10D, "scaling": Ackley10D_Scaling, "dim": 10},
    "GKXWC1": {"function": GKXWC1, "scaling": GKXWC1_Scaling, "dim": 2},
    "GKXWC2": {"function": GKXWC2, "scaling": GKXWC2_Scaling, "dim": 2},
    "JLH1": {"function": JLH1, "scaling": JLH1_Scaling, "dim": 2},
    "JLH2": {"function": JLH2, "scaling": JLH2_Scaling, "dim": 2},
    "Keane Bump": {"function": KeaneBump, "scaling": KeaneBump_Scaling, "dim": 18},
    "Three Truss": {"function": ThreeTruss, "scaling": ThreeTruss_Scaling, "dim": 2},
    "Compression Spring": {"function": CompressionSpring, "scaling": CompressionSpring_Scaling, "dim": 3},
    "Reinforced Concrete Beam": {"function": ReinforcedConcreteBeam, "scaling": ReinforcedConcreteBeam_Scaling, "dim": 3},
    "Pressure Vessel": {"function": PressureVessel, "scaling": PressureVessel_Scaling, "dim": 4},
    "Speed Reducer": {"function": SpeedReducer, "scaling": SpeedReducer_Scaling, "dim": 4},
    "Welded Beam": {"function": WeldedBeam, "scaling": WeldedBeam_Scaling, "dim": 4},
    "Heat Exchanger": {"function": HeatExchanger, "scaling": HeatExchanger_Scaling, "dim": 8},
    "Cantilever Beam": {"function": CantileverBeam, "scaling": CantileverBeam_Scaling, "dim": 10},
    "Car": {"function": Car, "scaling": Car_Scaling, "dim": 11},
    
    # Add more functions here
}





with gr.Blocks(theme=gr.themes.Default()) as demo:
    # Centered Title and Description using gr.HTML
    gr.HTML(
        """
        <div style="text-align: center;">
            <h1>Pre-trained Transformer for Constrained Bayesian Optimization</h1>
            <p>This is a demo for Bayesian Optimization using PFN (Prior-Data Fitted Networks). 
            Select your objective function by clicking on one of the check boxes below, then enter the iteration number to run the optimization process. 
            The results will be visualized in the radar chart and convergence plot.</p>
            <img src="https://github.com/rosenyu304/BOEngineeringBenchmark/blob/main/Icons.png?raw=true" 
                 alt="Example Image" 
                 style="width: 800px; height: auto; margin-top: 20px; display: block; margin-left: auto; margin-right: auto;">

        </div>
        """
    )

    selected_objective = gr.State(None)  # To store the selected objective function





    
    with gr.Row():
        
        objective_checkbox_group = gr.CheckboxGroup(
            choices=["JLH1", "JLH2", "GKXWC1", "GKXWC2", "Ackley2D", "Ackley6D", "Ackley10D", "Keane Bump", "Three Truss", "Reinforced Concrete Beam", "Pressure Vessel", "Welded Beam", "Speed Reducer", "Car"],
            label="Select the design problem:"
        )
    with gr.Row():
        iteration_input = gr.Number(label="Enter Iteration Number:", value=10)
            

    # Row for the Clear and Submit buttons
    with gr.Row():
        clear_button = gr.Button("Clear")
        submit_button = gr.Button("Submit", variant="primary")
        
    
    with gr.Row():
        with gr.Column():
            radar_plot = gr.Plot(label="Resulting Design")
        with gr.Column():
            convergence_plot = gr.Plot(label="Convergence Plot")



    # Define actions for buttons
    def clear_action():
        return None, None, None

    def submit_action(objective_function_choices, iteration_input):
        # Handle the case where multiple choices are selected
        if len(objective_function_choices) > 0:
            selected_function = objective_function_choices[0]  # Assuming using the first selected function
            return optimize(selected_function, iteration_input)
        return None, None

    # Button click actions
    clear_button.click(clear_action, outputs=[objective_checkbox_group, radar_plot, convergence_plot])
    submit_button.click(
        submit_action, 
        inputs=[objective_checkbox_group, iteration_input], 
        outputs=[radar_plot, convergence_plot]
    )

demo.launch(share=True)



Running on local URL:  http://127.0.0.1:7891
Running on public URL: https://f714b6f956fb581264.gradio.live

This share link expires in 72 hours. For free permanent hosting and GPU upgrades, run `gradio deploy` from Terminal to deploy to Spaces (https://huggingface.co/spaces)


In [1]:
import gradio as gr

def calculator(num1, operation, num2):
    if operation == "add":
        return num1 + num2
    elif operation == "subtract":
        return num1 - num2
    elif operation == "multiply":
        return num1 * num2
    elif operation == "divide":
        return num1 / num2

with gr.Blocks() as demo:
    with gr.Row():
        with gr.Column():
            num_1 = gr.Number(value=4)
            operation = gr.Radio(["add", "subtract", "multiply", "divide"])
            num_2 = gr.Number(value=0)
            submit_btn = gr.Button(value="Calculate")
        with gr.Column():
            result = gr.Number()

    submit_btn.click(
        calculator, inputs=[num_1, operation, num_2], outputs=[result], api_name=False
    )
    examples = gr.Examples(
        examples=[
            [5, "add", 3],
            [4, "divide", 2],
            [-4, "multiply", 2.5],
            [0, "subtract", 1.2],
        ],
        inputs=[num_1, operation, num_2],
    )

if __name__ == "__main__":
    demo.launch(show_api=False)

Running on local URL:  http://127.0.0.1:7899

To create a public link, set `share=True` in `launch()`.


In [50]:
import gradio as gr

def calculator(num1, operation, num2):
    if operation == "add":
        return num1 + num2
    elif operation == "subtract":
        return num1 - num2
    elif operation == "multiply":
        return num1 * num2
    elif operation == "divide":
        return num1 / num2

with gr.Blocks() as demo:
    with gr.Row():
        with gr.Column():
            num_1 = gr.Number(value=4)
            operation = gr.Radio(["add", "subtract", "multiply", "divide"])
            num_2 = gr.Number(value=0)
            submit_btn = gr.Button(value="Calculate")
        with gr.Column():
            result = gr.Number()

    submit_btn.click(
        calculator, inputs=[num_1, operation, num_2], outputs=[result], api_name=False
    )
    examples = gr.Examples(
        examples=[
            [5, "add", 3],
            [4, "divide", 2],
            [-4, "multiply", 2.5],
            [0, "subtract", 1.2],
        ],
        inputs=[num_1, operation, num_2],
    )

if __name__ == "__main__":
    demo.launch(show_api=False)

Running on local URL:  http://127.0.0.1:7890

To create a public link, set `share=True` in `launch()`.


In [36]:
# import gradio as gr

# def greet(selected_options):
#     return f"You selected: {', '.join(selected_options)}"

# with gr.Blocks() as demo:
#     with gr.Row():
#         checkbox_group = gr.CheckboxGroup(
#             choices=["Option 1", "Option 2"],
#             label="Select your options",
#             elem_id="custom_checkbox_group"
#         )
#         output = gr.Textbox(label="Output")
    
#     checkbox_group.change(greet, checkbox_group, output)

#     gr.HTML(
#         f"""
#         <style>
#         #custom_checkbox_group label {
#             display: block;
#             width: 200pt;
#             height: 200pt;
#             border: 1px solid #ccc;
#             margin-bottom: 10pt;
#             padding: 10pt;
#             box-sizing: border-box;
#             position: relative;
#         }
#         #custom_checkbox_group label input {
#             position: absolute;
#             top: 10pt;
#             left: 10pt;
#         }
#         #custom_checkbox_group label span {
#             position: absolute;
#             top: 10pt;
#             left: 40pt; /* Adjust this value to control the distance between the checkbox and the label */
#         }
#         #custom_checkbox_group label img {
#             position: absolute;
#             bottom: 10pt;
#             left: 10pt;
#             width: 180pt; /* Adjust the size of the image if needed */
#             height: auto;
#         }
#         </style>
#         <label>
#             <input type="checkbox" />
#             <span>Option 1</span>
#             <img src="https://images.pexels.com/photos/1108099/pexels-photo-1108099.jpeg" alt="Dog image"/>
#         </label>
#         """
#     )

# demo.launch()
